In [117]:
import pyodbc
import pandas as pd

In [118]:
pyodbc.drivers()

['PostgreSQL',
 'MySQL',
 'MySQL-5',
 'FreeTDS',
 'MariaDB',
 'ODBC Driver 18 for SQL Server',
 'ODBC Driver 17 for SQL Server']

In [119]:
conn = pyodbc.connect(
    Driver = '{ODBC Driver 18 for SQL Server}',
    Server = 'localhost',
    Database = 'DbFilme',
    Encrypt = 'Yes',
    TrustServerCertificate = 'Yes',
    UID = 'SA',
    PWD = 'Pg1024_JH', # Sua senha do Banco de Dados Local no SQL Server
    timeout=60
)

cursor = conn.cursor()

In [120]:
df = pd.read_csv("arquivos/consolidated/movies_consolidado.csv")

In [121]:
df.head()

id                             title releaseDate         rating  \
0  2000556032                          Aftersun  2022-10-21              R   
1  2000556064                               TÁR  2022-10-07              R   
2  2000556607                          No Bears  2022-12-23  Não informado   
3  2000556604  All the Beauty and the Bloodshed  2022-11-23        Unrated   
4  2000554951                      Hit the Road  2022-04-22  Não informado   

                genres                                        description  \
0                Drama  Sophie reflects on the shared joy and private ...   
1          Drama,Music  Set in the international world of classical mu...   
2        Drama,Romance  Two parallel love stories in which the partner...   
3  Documentary,History  All the Beauty and the Bloodshed is an epic, e...   
4   Comedy,Drama,Music  A family of four – two middle-aged parents and...   

   duration        tagline  metascore  metascore_count metascore_sentiment  \
0        98  Não informado         95               46   Universal acclaim   
1       158  Não informado         93               59   Universal acclaim   
2       106  Não informado         93               29   Universal acclaim   
3       113  Não informado         91               34   Universal acclaim   
4        93  Não informado         91               28   Universal acclaim   

   userscore  userscore_count  userscore_sentiment  \
0         80              256  Generally favorable   
1         75              246  Generally favorable   
2         80               23  Generally favorable   
3         78               26  Generally favorable   
4         72               27  Generally favorable   

                                production_companies         director  \
0  BBC Film,British Film Institute (BFI),Screen S...  Charlotte Wells   
1  Focus Features,Standard Film Company,EMJAG Pro...       Todd Field   
2  JP Production,Janus Film,Janus Films,ARP Sélec...     Jafar Panahi   
3  Participant,Praxis Films,I Wonder Pictures,Neo...    Laura Poitras   
4  Cherry Pickers Filmdistributie,Kino Lorber,Ang...     Panah Panahi   

            writer                                           top_cast  
0  Charlotte Wells  Paul Mescal,Frankie Corio,Celia Rowlson-Hall,S...  
1       Todd Field  Cate Blanchett,Noémie Merlant,Nina Hoss,Sophie...  
2     Jafar Panahi  Jafar Panahi,Naser Hashemi,Vahid Mobasseri,Bak...  
3    Não informado  Nan Goldin,David Velasco,Megan Kapler,Marina B...  
4     Panah Panahi  Pantea Panahiha,Mohammad Hassan Madjooni,Rayan...

In [122]:
df.columns

Index(['id', 'title', 'releaseDate', 'rating', 'genres', 'description',
       'duration', 'tagline', 'metascore', 'metascore_count',
       'metascore_sentiment', 'userscore', 'userscore_count',
       'userscore_sentiment', 'production_companies', 'director', 'writer',
       'top_cast'],
      dtype='object')

In [123]:
import time

block_size = 500 # quantidade de insert pra não explodir isso ai

# Monte de coisa pra driblar erro
def safe_int(value):
    try:
        if pd.isna(value):
            return None
        return int(value)
    except:
        return None

def safe_float(value):
    try:
        if pd.isna(value):
            return None
        return float(value)
    except:
        return None

def safe_str(value):
    if pd.isna(value):
        return None
    return str(value)

def safe_date(value):
    if pd.isna(value):
        return None
    if value == '0000-00-00':
        return None
    return value

In [124]:
c = 0

# A parte que insere os gêneros e os filmes
for row in df.itertuples():
    try:
        # Adiciona os gêneros se não existirem
        genres = [g.strip() for g in safe_str(row.genres).split(',')]
        for genre in genres:
            cursor.execute('SELECT COUNT(*) FROM genres WHERE genre_name = ?', genre)
            genre_exists = cursor.fetchone()[0] > 0
            if not genre_exists:
                cursor.execute('INSERT INTO genres (genre_name) VALUES (?)', genre)

        # Verifica se o filme já existe na tabela movies
        cursor.execute('SELECT COUNT(*) FROM movies WHERE movie_id = ?', row.id)
        movie_exists = cursor.fetchone()[0] > 0

        if not movie_exists:
            cursor.execute('''
                INSERT INTO movies (
                    movie_id, title, release_date, description,
                    duration, tagline, metascore, metascore_count,
                    userscore, userscore_count, userscore_sentiment,
                    production_companies, director, writer, top_cast)
                VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
            ''', (
                row.id,
                safe_str(row.title),
                safe_date(row.releaseDate),
                safe_str(row.description),
                safe_int(row.duration),
                safe_str(row.tagline),
                safe_int(row.metascore),
                safe_int(row.metascore_count),
                safe_int(row.userscore),
                safe_int(row.userscore_count),
                safe_str(row.userscore_sentiment),
                safe_str(row.production_companies),
                safe_str(row.director),
                safe_str(row.writer),
                safe_str(row.top_cast)
            ))

        # Para cada gênero relacionado ao filme, insere na tabela movie_genres
        cursor.execute('SELECT genres_id FROM genres WHERE genre_name = ?', genre)
        genres_id = cursor.fetchone()[0]

        cursor.execute('''
            INSERT INTO movie_genres (movie_id, genre_id)
            VALUES (?, ?)
        ''', (row.id, genres_id))
        c += 1
        if c % block_size == 0:
            conn.commit()
            time.sleep(0.1)  # pausa para aliviar o servidor

    except Exception as e:
        print(f"Erro ao inserir linha: {row}\n→ {e}")

# Commit final
conn.commit()
print('Finalizado!')


Erro ao inserir linha: Pandas(Index=0, id=2000556032, title='Aftersun', releaseDate='2022-10-21', rating='R', genres='Drama', description='Sophie reflects on the shared joy and private melancholy of a holiday she took with her father twenty years earlier. Memories real and imagined fill the gaps between miniDV footage as she tries to reconcile the father she knew with the man she didn’t.', duration=98, tagline='Não informado', metascore=95, metascore_count=46, metascore_sentiment='Universal acclaim', userscore=80, userscore_count=256, userscore_sentiment='Generally favorable', production_companies='BBC Film,British Film Institute (BFI),Screen Scotland,Tango Entertainment (III),PASTEL,Unified Theory,AZ Celtic Films,MUBI,A24,Andrews Film,Anticipate Pictures,Cinemanse,Condor,DCM Film Distribution,DDDream,Elástica Films,Exponenta,Film Development Council of the Philippines,Green Narae Media,Happinet Phantom Studios,Kismet Movies,Kismet Movies,Leopardo Filmes,Lev Cinemas,M2 Films,O2 Play,Ou

OperationalError: ('08S01', '[08S01] [Microsoft][ODBC Driver 18 for SQL Server]Communication link failure (-2147467259) (SQLEndTran)')

In [125]:
df = pd.read_csv("arquivos/consolidated/movies_reviews_consolidado.csv")

In [126]:
df.head()

id           title  \
0  2000545497  Dekalog (1988)   
1  2000548059     Rear Window   
2  2000548059     Rear Window   
3  2000548059     Rear Window   
4  2000548059     Rear Window   

                                               quote  score        date  \
0  The best 10 hours you will spend at movies and...    100  2021-05-01   
1  Best murder mystery ever. Modern. Simple. Diff...    100  2021-11-09   
2  One of the masterpieces and the best movie of ...    100  2021-03-16   
3  Story: 8/10...love the premise and the small c...     90  2021-09-28   
4  Film goes in crescendo, thanks to some great d...     80  2021-02-21   

            author publicationName review_type  
0     ItsMahdiyarr   Não informado        user  
1       Yannpastor   Não informado        user  
2  B4UShot-_-Vigil   Não informado        user  
3           jjauga   Não informado        user  
4            AJ_13   Não informado        user

In [127]:
df.columns

Index(['id', 'title', 'quote', 'score', 'date', 'author', 'publicationName',
       'review_type'],
      dtype='object')

In [128]:
for row in df.itertuples():
    try:
        cursor.execute('''
            INSERT INTO review (quote, score, publication_date, author, publication_name, review_type)
            VALUES(?,?,?,?,?,?)
        ''',(
            row.quote,
            row.score,
            row.date,
            row.author,
            row.publicationName,
            row.review_type
        ))
    except Exception as e:
        print("Erro ao inserir linha:", row)
        print(e)

conn.commit()

Erro ao inserir linha: Pandas(Index=0, id=2000545497, title='Dekalog (1988)', quote='The best 10 hours you will spend at movies and this Series.\n\n\nTen commandments. 10 episodes. 10 hours. When it first aired on Polish television in 1989, decades before long-form filmmaking would come to be regarded as the last bastion of auteurism, Krzysztof Kieślowski’s “Dekalog” was one of the most immense undertakings the cinema had ever seen. There had been longer works, and more lavishly financed ones — even when accounting for inflation, “Dekalog” would qualify as a micro-budget project — but the existential girth of Kieślowski’s magnum opus immediately made it feel like a monolith among molehills.', score=100, date='2021-05-01', author='ItsMahdiyarr', publicationName='Não informado', review_type='user')
('08S01', '[08S01] [Microsoft][ODBC Driver 18 for SQL Server]Communication link failure (0) (SQLPrepare)')
Erro ao inserir linha: Pandas(Index=1, id=2000548059, title='Rear Window', quote='Bes

KeyboardInterrupt: 